<a href="https://colab.research.google.com/github/unburied/DS-Unit-2-Tree-Ensembles/blob/master/Pumps.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

##Imports

In [0]:
%matplotlib inline
import matplotlib.pyplot as plt

In [3]:
!pip install pandas_profiling
!pip install category_encoders
!pip install plotly_express

In [0]:
import pandas as pd
import numpy as np

import category_encoders as ce
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split

from sklearn.preprocessing import LabelEncoder
from sklearn.tree import DecisionTreeClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.impute import SimpleImputer
from sklearn.decomposition import PCA

import plotly_express as px

In [0]:
def configure_plotly_browser_state():
  import IPython
  display(IPython.core.display.HTML('''
       <script src="/static/components/requirejs/require.js"></script>
       <script>
         requirejs.config({
           paths: {
             base: '/static/base',
             plotly: 'https://cdn.plot.ly/plotly-latest.min.js?noext',
           },
         });
       </script>
       '''))

In [6]:
!wget https://raw.githubusercontent.com/LambdaSchool/DS-Unit-2-Linear-Models/master/data/tanzania/train_features.csv
!wget https://raw.githubusercontent.com/LambdaSchool/DS-Unit-2-Linear-Models/master/data/tanzania/train_labels.csv
!wget https://raw.githubusercontent.com/LambdaSchool/DS-Unit-2-Linear-Models/master/data/tanzania/test_features.csv
!wget https://raw.githubusercontent.com/LambdaSchool/DS-Unit-2-Linear-Models/master/data/tanzania/sample_submission.csv

--2019-07-28 18:56:39--  https://raw.githubusercontent.com/LambdaSchool/DS-Unit-2-Linear-Models/master/data/tanzania/train_features.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 151.101.0.133, 151.101.64.133, 151.101.128.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|151.101.0.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 20054664 (19M) [text/plain]
Saving to: ‘train_features.csv.2’

train_features.csv. 100%[===================>]  19.12M  --.-KB/s    in 0.1s    

2019-07-28 18:56:39 (136 MB/s) - ‘train_features.csv.2’ saved [20054664/20054664]

--2019-07-28 18:56:40--  https://raw.githubusercontent.com/LambdaSchool/DS-Unit-2-Linear-Models/master/data/tanzania/train_labels.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 151.101.0.133, 151.101.64.133, 151.101.128.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|151.101.0.133|:443... connected.
HTTP req

In [0]:
import pandas_profiling as pp

##Fetch

In [0]:
#load dataframes
X = pd.read_csv('train_features.csv')
Y = pd.read_csv('train_labels.csv')

#Drop id's
Y = Y.status_group

In [0]:
#pp.ProfileReport(X)

##Baseline

In [10]:
#Split data
X_train, X_val, y_train, y_val = train_test_split(X, Y,random_state = 42,stratify = Y)
    
#Baseline
y_train.value_counts(normalize = True)

functional                 0.543075
non functional             0.384242
functional needs repair    0.072682
Name: status_group, dtype: float64

In [11]:
#get nums from df
numericals = X.select_dtypes('number').columns.to_list()
print(numericals)

['id', 'amount_tsh', 'gps_height', 'longitude', 'latitude', 'num_private', 'region_code', 'district_code', 'population', 'construction_year']


In [12]:
model = LogisticRegression(solver = 'lbfgs', multi_class = 'auto', max_iter = 350)
model.fit(X_train[numericals],y_train)
model.score(X_val[numericals], y_val)

/usr/local/lib/python3.6/dist-packages/sklearn/linear_model/logistic.py:947: ConvergenceWarning:

lbfgs failed to converge. Increase the number of iterations.



0.5484848484848485

In [0]:
#plot coefficent values for each label
fig = plt.figure(figsize = (30,5))

ax = fig.add_subplot(131)
coeffs = pd.Series(model.coef_[0], numericals)
ax = coeffs.sort_values().plot.barh()
ax.set_title(model.classes_[0], color = 'g')

ax1 = fig.add_subplot(132)
coeffs = pd.Series(model.coef_[1], numericals)
ax1 = coeffs.sort_values().plot.barh()
ax1.set_title(model.classes_[1], color = 'y')

ax2 = fig.add_subplot(133)
coeffs = pd.Series(model.coef_[2], numericals)
ax2 = coeffs.sort_values().plot.barh()
ax2.set_title(model.classes_[2], color = 'r')

plt.show();

It looks like longitude and region code have some of the largest effects on the model based on the coefficients

##PreProcessing Functions


In [0]:
def get_elevations(x):
#store each region and gps height in dict
  elevations = {}
  for region in x.region.unique():
    elevations[region] = x[x.region == region]['gps_height'].median()

#These looks to be the problem areas. The median values for these regions should not be zeo
  zero_regions = ['Dodoma', 'Kagera', 'Mbeya', 'Mwanza', 'Shinyanga', 'Tabora']

#I looked up the elevations and imputed the data
  elevations['Dodoma'] = 1118
  elevations['Kagera'] = 1500
  elevations['Mbeya'] = 1700
  elevations['Mwanza'] = 1140
  elevations['Shinyanga'] = 1128
  elevations['Tabora'] = 1191

#Use new values to clean zeroes in df based on imputed values
  for key in elevations:
    if key in zero_regions:
      x.loc[x.region == key, 'gps_height'] = elevations[key]
  
  return x

In [0]:
def get_dates(x):
  #reassgin as datetime object
  x.date_recorded = pd.to_datetime(x.date_recorded,
                                   infer_datetime_format= True)
  
  #split values and add to df
  x['year_rec'] = x.date_recorded.dt.year
  x['age'] = x.year_rec - x.construction_year 
  
  #drop dates(not working with standard scaler?)
  x = x.drop('date_recorded', axis = 1)
  
  return x

In [0]:
#Impute population based on current data
def get_pops(x):  
  #These are HALF the current estimates for population
  region_pops = {'Dodoma' : 1050000, 'Kagera' : 1229000, 'Shinyanga': 767500,
                 'Mbeya' : 135000, 'Tabora': 113500, 'Mwanza' : 1350000}

  #Get means for regions using estimates and the std of the set for consistency
  for region,pop in region_pops.items():
    size = x.loc[x.region == region, 'population'].size
    mean =   pop / size
    std = x.population.std()

  #function will use Gaussian distribution to impute value at each location
    def pop_imputer(n):
      random = np.random.normal()
      impute = mean + (random * std) + n

      #Ensure value is not less than zero, if so rerun func
      if impute < 0:
        pop_imputer(n)
      else:
        return int(impute)

    x.loc[x.region == region, 'population'] = x.loc[x.region == region,
                                               'population'].apply(pop_imputer)


  return x

In [0]:
def coordinates(x):
#eliminate null island values
  x['latitude'] = x['latitude'].replace(-2e-08, -2)

  #These locations contain ALL zero values for longitude
  locations = {'Magu' : 33.4444, 'Geita' : 32.2314, 'Bariadi' : 33.9833}
  
  for key,val in locations.items():
    x.loc[x.lga == key, 'longitude'] = val
  
  return x

In [0]:
def clean(df):
  x = df.copy()

#Clean zeroes in data
  if 'construction_year' in x.columns:
    x['construction_year'] = x.construction_year.replace(0, np.nan)
    x['construction_year'] = np.where(x.construction_year.isnull(),
                                   x.construction_year.mode(),
                                   x.construction_year)     
#reassign date values and impute elevation, population, and longitude data      
  if 'date_recorded' in x.columns:
    x = get_dates(x)
  if 'gps_height' in x.columns:
    x = get_elevations(x)
  if 'population' in x.columns:
    x = get_pops(x)
  if 'longitude' in x.columns:
    x = coordinates(x)

  #reassign bool values
  if 'permit' in x.columns:
    x['permit'] = np.where(x.permit == True , 1,0)
  if 'public_meeting' in x.columns:
    x['public_meeting'] = np.where(x.public_meeting == True , 1,0)

  #check for and replace unknowns and other with NAN
  for col in x.columns:
    if x[col].dtype == object:
      x[col] = np.where(x[col] == 'other', np.nan, x[col])
      x[col] = np.where(x[col] == 'unknown', np.nan, x[col])
  
  #drop items both high card and duplicates
    dropping = ['quantity_group', 'recorded_by','subvillage', 'wpt_name',
            'management_group']  
    if col in dropping:
      x = x.drop(columns = col)

  return x


In [0]:
#replcae categorical values and scale data
def encode_data(train, val): 
  #split object columns based on cardinality
  objs = train.select_dtypes('object').columns.tolist()
  hots = [col for col in objs if train[col].nunique() <= 10]
  ordins = [col for col in objs if train[col].nunique() > 10]
    
  #encode low card obj with onehotencoder
  ohe = ce.OneHotEncoder(use_cat_names=True, cols = hots, )
  train = ohe.fit_transform(train)
  val = ohe.transform(val)
  
  #encode high card obj with ordinal encoder
  enc = ce.OrdinalEncoder(return_df = True, cols = ordins, )
  train= enc.fit_transform(train)
  val = enc.transform(val)

  #Scale data
  scaled = StandardScaler()
  train_scale = scaled.fit_transform(train)
  val_scale = scaled.transform(val)
  
  #Ensure columns are maintained
  train = pd.DataFrame(train_scale, columns = train.columns)
  val = pd.DataFrame(val_scale, columns = val.columns)
  
  return train, val

In [0]:
def imputer(train, val):
  cols = train.columns.tolist()
  si = SimpleImputer()
  
  train = train.copy()
  val = val.copy()
  
  train = si.fit_transform(train)
  val = si.transform(val)
  
  train = pd.DataFrame(train, columns = cols)
  val = pd.DataFrame(val, columns = cols)
  
  return train, val

In [0]:
def split_data(X,Y):  
  #Split data
  X_train, X_val, y_train, y_val = train_test_split(X, Y,
                                              random_state = 42,stratify = Y)
  
  return [X_train, X_val, y_train, y_val]

In [0]:
def decompose(train,val):
  #perform pca on data
  pca = PCA()
  train = pca.fit_transform(train)
  val = pca.transform(val)
  
  return train, val

In [0]:
#Pipeline to encode, scale, split 
def pipeline(X, y = None, encode = False, impute = False,
             test = None, split = False, pca = False):
  
  target_supplied = False
  test_transformation_requested = False
  
  #preprocess data 
  x = clean(X) 
  
  #check if split is requested, that a target vector is also supplied
  if split and type(y) == pd.Series:
    target_supplied = True
    
  #load and clean test data if included(for submission purposes) 
  if type(test) == pd.DataFrame:
    test = test = clean(test)
    test_transformation_requested = True  
    
  #performm train test split on data
  if target_supplied:
    data = split_data(x,y) 
    
  #encode categorical data
  if encode and target_supplied:
    data[0], data[1] = encode_data(data[0], data[1])  
  if encode and test_transformation_requested:
    x, test = encode_data(x, test)  
    
  #implement simple imputer
  if impute and target_supplied:
    data[0], data[1] = imputer(data[0], data[1])
  if impute and test_transformation_requested:
    x, test = imputer(x, test)       
    
  #perform pca decomposition  
  if pca and target_supplied:
    data[0], data[1] = decompose(data[0], data[1])
  if pca and test_transformation_requested:
    x, test = decompose(x, test)
  
  if target_supplied:
    return data
  elif test_transformation_requested:
    return x, test

##Preliminary Models

In [0]:
#test and score each model
def model_score(model, data):
  X_train = data[0] 
  X_val = data[1]
  y_train = data[2]
  y_val = data[3]
  
  model.fit(X_train,y_train)
  y_pred = model.predict(X_val)
  
  return accuracy_score(y_val, y_pred)

In [0]:
#run dfs through pipeline
data = pipeline(X, y = Y ,encode = True, impute = True, split = True)

In [26]:
#instantiate models
dt = DecisionTreeClassifier()
gbm = GradientBoostingClassifier()
knn = KNeighborsClassifier()
rfc = RandomForestClassifier(n_estimators= 150)

#get and print scores
print(f'Tree - {model_score(dt, data)}')
print(f'Boost - {model_score(gbm, data)}')
print(f'Neighbor - {model_score(knn, data)}')
print(f'Forest - {model_score(rfc, data)}')

Tree - 0.737912457912458
Boost - 0.7552188552188552
Neighbor - 0.7695622895622896
Forest - 0.8127272727272727


Its looks like Random Forest will give us a good score right from the start. 

##Feature Exploration

In [0]:
fig = plt.figure(figsize = (7,7))

importance = pd.Series(rfc.feature_importances_, data[0].columns)
importance.sort_values(ascending = True)[86:].plot.barh();

In [0]:
fe = clean(X.copy())
fe = fe.join(Y)
fe = fe.fillna(method ='ffill')

In [29]:
configure_plotly_browser_state()

In [30]:
px.scatter(fe, x = 'longitude',y= 'latitude', color = 'quantity', 
            size = 'population', facet_col = 'status_group',
           title = 'Quantity, Population, and Functionality')

In [31]:
fe.quantity.value_counts()

enough          33615
insufficient    15370
dry              6320
seasonal         4095
Name: quantity, dtype: int64

In [32]:
px.scatter(fe, x = 'longitude',y= 'latitude', color = 'extraction_type_class', 
           size = 'population' , facet_col = 'status_group',
           title = 'Extraction Type, Population, and Functionality', )

In [33]:
fe.extraction_type_class.value_counts()

gravity         30021
handpump        18515
submersible      6932
motorpump        3301
rope pump         507
wind-powered      124
Name: extraction_type_class, dtype: int64

In [34]:
px.scatter(fe, x = 'longitude',y= 'latitude', color = 'waterpoint_type_group', 
           size = 'population',  facet_col = 'status_group',
           title = 'Waterpoint Type, Population, and Functionality', )

In [35]:
fe.waterpoint_type_group.value_counts()

communal standpipe    38749
hand pump             19624
improved spring         889
cattle trough           131
dam                       7
Name: waterpoint_type_group, dtype: int64

In [36]:
px.scatter(fe, x = 'longitude',y= 'latitude', color = 'gps_height', 
           facet_col = 'status_group',
           title = 'Elevation and Functionality', )

In [37]:
fe.quality_group.value_counts()

good        52483
salty        5370
milky         822
colored       505
fluoride      220
Name: quality_group, dtype: int64

##Feature Selection

In [38]:
features = ['waterpoint_type_group', 'extraction_type_class', 'quantity',
            'latitude', 'longitude', 'gps_height', 'region', 'population',
            'lga', 'construction_year', 'date_recorded']
columns = ['quantity_seasonal','waterpoint_type_group_cattle trough',
           'waterpoint_type_group_dam', 'extraction_type_class_wind-powered']

x = X.copy()
data = pipeline(x[features], y = Y, split = True,  encode = True, impute = True)

data[0] = data[0].drop(columns = columns)
data[1] = data[1].drop(columns = columns)         

rfc = RandomForestClassifier(n_estimators=150, n_jobs = -1)
model_score(rfc, data)

0.7934680134680134

In [0]:
fig = plt.figure(figsize = (7,7))

importance = pd.Series(rfc.feature_importances_, data[0].columns)
importance.sort_values(ascending = True).plot.barh();

##Feature Engineering 

In [0]:
#get slightly less granular population based on lga
fe['median_pop_at_lga'] = fe.population

for lga in fe.lga.unique():
  fe.loc[fe.lga == lga ,'median_pop_at_lga'] = fe[fe.lga == lga]['population'].median()

In [0]:
from sklearn.model_selection import KFold

In [0]:
x , _ = pipeline(X, test = X, encode = True, impute = True)

In [0]:
kf = KFold(5)

predictions = {'rfc' : [], 'gbm': [], 'knn': []} 
models = {'rfc':RandomForestClassifier(n_estimators= 150), 
          'gbm':GradientBoostingClassifier(),
          'knn':KNeighborsClassifier()}


for train, test in kf.split(x):
  X_train, X_test = x.iloc[train], x.iloc[test]
  y_train  = Y.iloc[train]
  
  for name,model in models.items():
    model.fit(X_train, y_train)
    y_pred = model.predict(X_test)
    predictions[name].append(y_pred)
      
for key,val in predictions.items():
  x[key] = val


##Submission


In [0]:
#fetch test data for submission
#test = pd.read_csv('test_features.csv')
sample_submission = pd.read_csv('sample_submission.csv')

In [0]:
#clean and preprocess data
def transform(df):
  features = ['waterpoint_type_group', 'extraction_type_class', 'quantity',
              'latitude', 'longitude', 'gps_height', 'region', 'population',
              'lga', 'construction_year']
  x = df[features].copy()

  x = get_elevations(x)
  x = get_pops(x)
  x = coordinates(x)

  x['construction_year'] = x.construction_year.replace(0, np.nan)
  x.construction_year = np.where(x.construction_year.isnull(),
                                 x.construction_year.mode(),
                                 x.construction_year)

  #x = x.drop(['lga','region'], axis = 1)
  x = encode_df(x)

  x = x.fillna(method = 'ffill')
  x = x.drop(['waterpoint_type_group_other', 'extraction_type_class_other',
              'quantity_seasonal', 'quantity_unknown',
              'waterpoint_type_group_cattle trough', 'waterpoint_type_group_dam',
              'extraction_type_class_wind-powered'], axis = 1)
  
  return x

In [0]:
X, test = pipeline(X, test = test, encode = True, impute = True)

In [0]:
forest = RandomForestClassifier(n_estimators=150)

forest.fit(X, Y)
y_pred = forest.predict(test)

In [0]:
from google.colab import files

submission = sample_submission.copy()
submission['status_group'] = y_pred
submission.to_csv('submission-03.csv', index=False)


files.download('submission-03.csv')